# Data Science and Visualization (RUC F2023)

## Lecture 9: Associate Rules

 # Apriori Algorithm for Association Rule Mining
 
 This notebook demonstrates how to use the library **mlxtend** to mine association rules.
 
 To install mlxtend, you need to execute the following in Anaconda Prompt:

pip install mlxtend

## 0. Setup and data loading

In [18]:
import numpy as np
import pandas as pd
#from apyori import apriori

# To make sure the first row is not thought of as the heading
dataset = pd.read_csv('C:/Data/store_data.csv', header=None) 
dataset.shape

(7501, 20)

Let's take a look at the format of the dataset:

In [19]:
dataset.head()

0          1           2                 3             4   \
0         shrimp    almonds     avocado    vegetables mix  green grapes   
1        burgers  meatballs        eggs               NaN           NaN   
2        chutney        NaN         NaN               NaN           NaN   
3         turkey    avocado         NaN               NaN           NaN   
4  mineral water       milk  energy bar  whole wheat rice     green tea   

                 5     6               7             8             9   \
0  whole weat flour  yams  cottage cheese  energy drink  tomato juice   
1               NaN   NaN             NaN           NaN           NaN   
2               NaN   NaN             NaN           NaN           NaN   
3               NaN   NaN             NaN           NaN           NaN   
4               NaN   NaN             NaN           NaN           NaN   

               10         11     12     13             14      15  \
0  low fat yogurt  green tea  honey  salad  mineral water  salmon   
1             NaN        NaN    NaN    NaN            NaN     NaN   
2             NaN        NaN    NaN    NaN            NaN     NaN   
3             NaN        NaN    NaN    NaN            NaN     NaN   
4             NaN        NaN    NaN    NaN            NaN     NaN   

                  16               17       18         19  
0  antioxydant juice  frozen smoothie  spinach  olive oil  
1                NaN              NaN      NaN        NaN  
2                NaN              NaN      NaN        NaN  
3                NaN              NaN      NaN        NaN  
4                NaN              NaN      NaN        NaN

Each row represents a transaction. The columns do not carry any meanings here, as the values in a same column do NOT represent the same thing or the same type.

Also, we can see there are many NULL or missing values on each row. Let's count them:

In [4]:
pd.set_option('display.max_rows', None)

dataset.isnull().sum(axis=1)

0        0
1       17
2       19
3       18
4       15
5       19
6       18
7       17
8       17
9       19
10      18
11      19
12      15
13      17
14      18
15      19
16      13
17      18
18      10
19      15
20      13
21      18
22      14
23      12
24      19
25      14
26      11
27      19
28      15
29      16
30      16
31      16
32      17
33      17
34      19
35      16
36      18
37      17
38      17
39      17
40      19
41      12
42      19
43      16
44      19
45      12
46      16
47      18
48      18
49      17
50      15
51      17
52      18
53      18
54      17
55      18
56       9
57      18
58      13
59      14
60      19
61      19
62      19
63      15
64      18
65      19
66      18
67      13
68      19
69      18
70      15
71      17
72      19
73      19
74      18
75      19
76      17
77      18
78      15
79      19
80      17
81      15
82      16
83      14
84      19
85      18
86      18
87      19
88      18
89      16
90      19

In [21]:
del dataset[dataset.columns[0]]

dataset.head()

Let's see how many items on each row/transaction:

In [26]:
dataset.count(axis='columns')

0       19
1        2
2        0
3        1
4        4
5        0
6        1
7        2
8        2
9        0
10       1
11       0
12       4
13       2
14       1
15       0
16       6
17       1
18       9
19       4
20       6
21       1
22       5
23       7
24       0
25       5
26       8
27       0
28       4
29       3
30       3
31       3
32       2
33       2
34       0
35       3
36       1
37       2
38       2
39       2
40       0
41       7
42       0
43       3
44       0
45       7
46       3
47       1
48       1
49       2
50       4
51       2
52       1
53       1
54       2
55       1
56      10
57       1
58       6
59       5
60       0
61       0
62       0
63       4
64       1
65       0
66       1
67       6
68       0
69       1
70       4
71       2
72       0
73       0
74       1
75       0
76       2
77       1
78       4
79       0
80       2
81       4
82       3
83       5
84       0
85       1
86       1
87       0
88       1
89       3
90       0

## 1. Data preparation

We first transform the dataset into a transaction table in the format of *a list of lists*. A small example is given below. Notice the two levles of '[ ]' pairs:

[['Milk', 'Onion', 'Nutmeg', 'Kidney Beans', 'Eggs', 'Yogurt'],

['Dill', 'Onion', 'Nutmeg', 'Kidney Beans', 'Eggs', 'Yogurt'],

['Milk', 'Apple', 'Kidney Beans', 'Eggs'],

['Milk', 'Unicorn', 'Corn', 'Kidney Beans', 'Yogurt'],

['Corn', 'Onion', 'Onion', 'Kidney Beans', 'Ice cream', 'Eggs']]

This intermediate format is needed by the function to be used in subsequent operations.

In [30]:
transactions = []

# We loop on all rows, i.e., transactions, in the original dataset
for i in range(0, dataset.shape[0]):
    # We transform the current transaction/row
    transaction = []
    # We loop on all values on the current row
    for j in range(0, dataset.shape[1]):
        # We get the current value on this row
        item = dataset.iloc[i, j]
        # If the value is NULL, we know there're no more values on this row, so we break out of the inner loop
        if (pd.isnull(item)):
            break
        else:
            # Otherwise, we add this concrete value/item to the end of the value for the current transaction
            transaction.append(item)
        
    transactions.append(transaction)

# Let's see the 2nd transaction in the transaction table
print(transactions[1])

['meatballs', 'eggs']


The **apriori()** function from **mlxtend.frequent_patterns** expects data in a pandas DataFrame of a speical format, where
* the dimenions are all the items 
* each transaction is represented by a series of boolean values: True (or False) indicates a corresponding item is available (or unavailable) in the transaction.

Therefore we need to transform the original transaection table. This is done by the **TransactionEncoder()**:

In [31]:
from mlxtend.preprocessing import TransactionEncoder

te = TransactionEncoder()
# The two steps, fit and transform, can be merged into one step
#te_ary = te.fit(dataset).transform(dataset)
te_ary = te.fit_transform(transactions)

# We generate a DataFrame for the transformed dataset
df = pd.DataFrame(te_ary, columns=te.columns_)
df

asparagus  almonds  antioxydant juice  asparagus  avocado  babies food  \
0          False     True               True      False     True        False   
1          False    False              False      False    False        False   
2          False    False              False      False    False        False   
3          False    False              False      False     True        False   
4          False    False              False      False    False        False   
5          False    False              False      False    False        False   
6          False    False              False      False    False        False   
7          False    False              False      False    False        False   
8          False    False              False      False    False        False   
9          False    False              False      False    False        False   
10         False    False              False      False    False        False   
11         False    False              False      False    False        False   
12         False    False              False      False    False        False   
13         False    False              False      False    False        False   
14         False    False              False      False    False        False   
15         False    False              False      False    False        False   
16         False    False              False      False    False        False   
17         False    False              False      False    False        False   
18         False    False              False      False    False        False   
19         False    False              False      False    False        False   
20         False    False              False      False    False        False   
21         False    False              False      False    False        False   
22         False    False              False      False    False        False   
23         False    False              False      False     True        False   
24         False    False              False      False    False        False   
25         False    False              False      False     True        False   
26         False    False              False      False    False        False   
27         False    False              False      False    False        False   
28         False    False              False      False    False        False   
29         False    False              False      False    False        False   
30         False    False              False      False    False        False   
31         False    False              False      False     True        False   
32         False    False              False      False    False        False   
33         False    False              False      False    False        False   
34         False    False              False      False    False        False   
35         False    False              False      False    False        False   
36         False    False              False      False    False        False   
37         False    False              False      False    False        False   
38         False    False              False      False    False        False   
39         False    False              False      False    False        False   
40         False    False              False      False    False        False   
41         False    False              False      False    False        False   
42         False    False              False      False    False        False   
43         False    False              False      False    False        False   
44         False    False              False      False    False        False   
45         False    False              False      False     True        False   
46         False    False              False      False    False        False   
47         False    False              False      False    False        False   
48         False    False             

In [32]:
len(df.columns)

120

In the transformed data, the columns make sense: they're just the item names:

In [33]:
df.columns

Index([' asparagus', 'almonds', 'antioxydant juice', 'asparagus', 'avocado',
       'babies food', 'bacon', 'barbecue sauce', 'black tea', 'blueberries',
       ...
       'turkey', 'vegetables mix', 'water spray', 'white wine',
       'whole weat flour', 'whole wheat pasta', 'whole wheat rice', 'yams',
       'yogurt cake', 'zucchini'],
      dtype='object', length=120)

## 2. Generating Frequent Itemsets

Now, let us return the frequent itemsets with at least 1% support:

In [34]:
from mlxtend.frequent_patterns import apriori

frequent_itemsets = apriori(df, min_support=0.01, use_colnames=True)

frequent_itemsets

support                                 itemsets
0    0.018931                                (almonds)
1    0.025730                                (avocado)
2    0.010399                         (barbecue sauce)
3    0.013065                              (black tea)
4    0.011332                             (body spray)
5    0.030663                               (brownies)
6    0.010399                                (burgers)
7    0.023197                                 (butter)
8    0.067991                                   (cake)
9    0.014931                                (carrots)
10   0.022397                                (cereals)
11   0.038262                              (champagne)
12   0.054126                                (chicken)
13   0.111718                              (chocolate)
14   0.044394                                (cookies)
15   0.048260                            (cooking oil)
16   0.029596                         (cottage cheese)
17   0.012932                               (eggplant)
18   0.142514                                   (eggs)
19   0.018131                             (energy bar)
20   0.024263                           (energy drink)
21   0.060259                               (escalope)
22   0.010932                   (extra dark chocolate)
23   0.138382                           (french fries)
24   0.020131                            (french wine)
25   0.041195                            (fresh bread)
26   0.011732                          (fromage blanc)
27   0.059059                        (frozen smoothie)
28   0.045594                      (frozen vegetables)
29   0.013332                          (grated cheese)
30   0.119184                              (green tea)
31   0.069191                            (ground beef)
32   0.011865                                   (gums)
33   0.010932                                    (ham)
34   0.018531                          (herb & pepper)
35   0.043861                                  (honey)
36   0.028663                               (hot dogs)
37   0.014931                            (light cream)
38   0.025730                             (light mayo)
39   0.070391                         (low fat yogurt)
40   0.010265                              (magazines)
41   0.016531                              (meatballs)
42   0.010932                                 (melons)
43   0.105453                                   (milk)
44   0.161445                          (mineral water)
45   0.016131                                   (mint)
46   0.014931                                (muffins)
47   0.018131                   (mushroom cream sauce)
48   0.019864                                    (oil)
49   0.056926                              (olive oil)
50   0.084389                               (pancakes)
51   0.013065                        (parmesan cheese)
52   0.014131                                  (pasta)
53   0.018398                                 (pepper)
54   0.016664                            (protein bar)
55   0.011732                               (red wine)
56   0.017464                                   (rice)
57   0.038662                                 (salmon)
58   0.028130                                 (shrimp)
59   0.040128                                   (soup)
60   0.126916                              (spaghetti)
61   0.018131                           (strawberries)
62   0.028796                           (tomato juice)
63   0.010932                           (tomato sauce)
64   0.040128                               (tomatoes)
65   0.020531                         (vegetables mix)
66   0.015598                             (white wine)
67   0.016798                      (whole wheat pasta)
68   0.052260                       (whole wheat rice)
69   0.023197                            (yogurt cake)
70   0.017064                             (cake, eggs)
71   0.014265                     (cake, frenc

## 3. Generating Association Rules

We obtain the inferred rules in a dataframe, via function **association_rules()**:

In [35]:
from mlxtend.frequent_patterns import association_rules

rules = association_rules(frequent_itemsets, metric ="lift", min_threshold = 1)

rules

antecedents                   consequents  \
0                          (cake)                        (eggs)   
1                          (eggs)                        (cake)   
2                          (cake)                (french fries)   
3                  (french fries)                        (cake)   
4                          (cake)                   (green tea)   
5                     (green tea)                        (cake)   
6                          (cake)                        (milk)   
7                          (milk)                        (cake)   
8                          (cake)               (mineral water)   
9                 (mineral water)                        (cake)   
10                         (cake)                    (pancakes)   
11                     (pancakes)                        (cake)   
12                         (cake)                   (spaghetti)   
13                    (spaghetti)                        (cake)   
14                    (chocolate)                     (chicken)   
15                      (chicken)                   (chocolate)   
16                         (eggs)                     (chicken)   
17                      (chicken)                        (eggs)   
18                      (chicken)                (french fries)   
19                 (french fries)                     (chicken)   
20                    (green tea)                     (chicken)   
21                      (chicken)                   (green tea)   
22                         (milk)                     (chicken)   
23                      (chicken)                        (milk)   
24                (mineral water)                     (chicken)   
25                      (chicken)               (mineral water)   
26                      (chicken)                   (spaghetti)   
27                    (spaghetti)                     (chicken)   
28                    (chocolate)                 (cooking oil)   
29                  (cooking oil)                   (chocolate)   
30                         (eggs)                   (chocolate)   
31                    (chocolate)                        (eggs)   
32                     (escalope)                   (chocolate)   
33                    (chocolate)                    (escalope)   
34                    (chocolate)                (french fries)   
35                 (french fries)                   (chocolate)   
36              (frozen smoothie)                   (chocolate)   
37                    (chocolate)             (frozen smoothie)   
38                    (chocolate)           (frozen vegetables)   
39            (frozen vegetables)                   (chocolate)   
40                    (chocolate)                   (green tea)   
41                    (green tea)                   (chocolate)   
42                  (ground beef)                   (chocolate)   
43                    (chocolate)                 (ground beef)   
44               (low fat yogurt)                   (chocolate)   
45                    (chocolate)              (low fat yogurt)   
46                    (chocolate)                        (milk)   
47                         (milk)                   (chocolate)   
48                    (chocolate)               (mineral water)   
49                (mineral water)                   (chocolate)   
50                    (chocolate)                   (olive oil)   
51                    (olive oil)                   (chocolate)   
52                    (chocolate)                    (pancakes)   
53                     (pancakes)                   (chocolate)   
54                    (chocolate)                   (spaghetti)   
55                    (spaghetti)                   (chocolate)   
56                      (cookies)                (french fries)   
57                 (french fries)                     (cookies)   
58                      (cookies)                   (green tea)   
59

For **leverage** and **conviction**, please refer to http://rasbt.github.io/mlxtend/user_guide/frequent_patterns/association_rules/

We can sort the rules on confidence and lift:

In [36]:
rules = rules.sort_values(['confidence', 'lift'], ascending =[False, False])
rules.head()

antecedents      consequents  antecedent support  \
175                    (soup)  (mineral water)            0.040128   
138             (ground beef)  (mineral water)            0.069191   
214         (milk, spaghetti)  (mineral water)            0.029329   
207  (ground beef, spaghetti)  (mineral water)            0.029063   
195              (eggs, milk)  (mineral water)            0.025997   

     consequent support   support  confidence      lift  leverage  conviction  
175            0.161445  0.018531    0.461794  2.860377  0.012052    1.558056  
138            0.161445  0.030129    0.435453  2.697218  0.018959    1.485358  
214            0.161445  0.012665    0.431818  2.674705  0.007930    1.475857  
207            0.161445  0.012532    0.431193  2.670831  0.007840    1.474234  
195            0.161445  0.011199    0.430769  2.668208  0.007001    1.473137

### References
* http://rasbt.github.io/mlxtend/user_guide/frequent_patterns/apriori/
* https://www.geeksforgeeks.org/implementing-apriori-algorithm-in-python/
* http://rasbt.github.io/mlxtend/user_guide/frequent_patterns/association_rules/